In [1]:
import requests
import pandas as pd

# financialmodelingprep API Endpoint
url = "https://financialmodelingprep.com/api/v3/financials/income-statement"

# API Request Parameters
params = {
    "apikey": "<86dd63f6b8ae774b061232685b78eb52>",
    "datatype": "json"
}

# Stock Tickers
tickers = ["REXR", "PSA", "DRE", "ESS", "AVR"]

# Data Fields to Collect
data_fields = ["Dividend per Share", "Net Income"]

# Data Dictionary to Store Results
data_dict = {}

# Loop through Tickers and Collect Data
for ticker in tickers:
    querystring = {"symbol": ticker}
    response = requests.get(url, params={**params, **querystring})
    if response.status_code == 200:
        json_data = response.json()
        if "financials" in json_data and len(json_data["financials"]) > 0:
            data = {}
            for field in data_fields:
                if field in json_data["financials"][0]:
                    data[field] = json_data["financials"][0][field]
                else:
                    data[field] = None
            data_dict[ticker] = data

# Convert Data Dictionary to Pandas Dataframe
df = pd.DataFrame.from_dict(data_dict, orient="index")

# Rename Dataframe Columns
df = df.rename(columns={"Dividend per Share": "dividendRate", "Net Income": "netIncomeToCommon"})

# Save Dataframe to CSV File on Desktop
df.to_csv("~/Desktop/stock_data.csv")

In [20]:
import yfinance as yf
import numpy as np
import datetime as dt

# 定义股票代码和目标价格
stock_symbol = 'tsla'
target_price = 166.00

# 获取过去一年的历史股票数据
end_date = dt.date.today()
start_date = end_date - dt.timedelta(days=3650)
stock_data = yf.download(stock_symbol, start=start_date, end=end_date)
returns = stock_data['Adj Close'].pct_change().dropna()

# 定义模拟次数和时间跨度
num_simulations = 100000
days = 10

# 计算均值和标准差
mu = returns.mean()
sigma = returns.std()

# 进行 Monte Carlo 模拟
simulated_prices = np.zeros(num_simulations)
for i in range(num_simulations):
    daily_returns = np.random.normal(mu, sigma, days)
    simulated_prices[i] = stock_data['Adj Close'][-1] * np.prod(1 + daily_returns)

# 计算目标价格的概率
if target_price >= stock_data['Adj Close'][-1]:
    probability = sum(simulated_prices >= target_price) / num_simulations
else:
    probability = sum(simulated_prices <= target_price) / num_simulations

print("在接下来的 {} 天内，股票价格达到 {} 美元的概率为 {:.2%}".format(days, target_price, probability))


[*********************100%***********************]  1 of 1 completed
在接下来的 10 天内，股票价格达到 166.0 美元的概率为 17.18%
